In [1]:
# read data
import pandas as pd
# Set the maximum number of rows and columns to display
pd.set_option('display.max_rows', 200)  # Adjust this number as needed
pd.set_option('display.max_columns', 50)  # Adjust this number as needed

In [2]:
df = pd.read_csv('../../data_CityEvent/Cityevents/Demand_Intelligence_for_Non_Attended_Events_California-0.csv')
df.shape

(20070, 32)

In [24]:
df['GEO'].isna().sum()

np.int64(0)

In [25]:
df['GEO'][3]

'{"coordinates":[[[-120.760378,36.20308500000003],[-120.76378999999996,36.20908499999998],[-120.766969,36.21005400000004],[-120.76531199999994,36.213481],[-120.76847799999997,36.21391600000002],[-120.77233100000001,36.220175],[-120.77601999999997,36.22012700000002],[-120.77866199999998,36.22319800000001],[-120.78127300000001,36.22244099999999],[-120.78065499999995,36.22482000000001],[-120.783249,36.229181999999966],[-120.78899799999996,36.230535],[-120.78928200000001,36.23500100000004],[-120.79371000000002,36.234305000000006],[-120.79526899999996,36.236557],[-120.79910000000004,36.235519999999994],[-120.802117,36.237751000000024],[-120.80074699999997,36.240283000000005],[-120.80547300000002,36.24016799999999],[-120.80733799999997,36.243788000000016],[-120.81216599999993,36.245194999999995],[-120.81077399999997,36.25170199999997],[-120.81356800000003,36.25019699999997],[-120.81448299999998,36.253257000000026],[-120.82030299999995,36.25378899999999],[-120.823715,36.257277000000016],[-120

In [6]:
# 3. assign CBGID to new event: get new col

import json
import geopandas as gpd
from shapely.geometry import Point

# Check and handle possible issues with coordinates
def create_point(geo):
    if isinstance(geo, dict) and 'coordinates' in geo:
        coords = geo['coordinates']
        if isinstance(coords, list) and len(coords) == 2 and all(isinstance(c, (int, float)) for c in coords):
            return Point(coords)  # Create Point only if coordinates are valid
    return None  # Return None if coordinates are invalid


In [6]:
df['GEO'][0]

'{"coordinates":[-117.1635759,32.8039378],"type":"Point"}'

In [7]:
import pandas as pd
import json
from shapely.geometry import shape

# Function to parse GEO column and create geometry
def parse_geo(geo_str):
    geo_dict = json.loads(geo_str)
    return shape(geo_dict)

# Apply the function to create the new 'geometry' column
df['geometry'] = df['GEO'].apply(parse_geo)

# Display the DataFrame
display(df[['GEO', 'geometry']])


GEO  \
0      {"coordinates":[-117.1635759,32.8039378],"type...   
1      {"coordinates":[-117.203114,33.887259],"type":...   
2      {"coordinates":[[[[-121.62471099999999,36.8124...   
3      {"coordinates":[[[-120.760378,36.2030850000000...   
4      {"coordinates":[[[[-122.41867557807998,37.8525...   
...                                                  ...   
20065  {"coordinates":[[[-120.96917499999998,38.16302...   
20066  {"coordinates":[[[-121.74643699999997,37.33889...   
20067  {"coordinates":[[[-122.05569299999995,39.86397...   
20068  {"coordinates":[[[-121.619522,38.5893599999999...   
20069  {"coordinates":[[[-119.718422,36.7077150000000...   

                                                geometry  
0                        POINT (-117.1635759 32.8039378)  
1                          POINT (-117.203114 33.887259)  
2      MULTIPOLYGON (((-121.62471099999999 36.8124840...  
3      POLYGON ((-120.760378 36.20308500000003, -120....  
4      MULTIPOLYGON (((-122.41867557807998 37.8525267...  
...                                                  ...  
20065  POLYGON ((-120.96917499999998 38.1630230000000...  
20066  POLYGON ((-121.74643699999997 37.3388930000000...  
20067  POLYGON ((-122.05569299999995 39.8639730000000...  
20068  POLYGON ((-121.619522 38.589359999999964, -121...  
20069  POLYGON ((-119.718422 36.707715000000036, -119...  

[20070 rows x 2 columns]

In [8]:
df['GEO'].isna().sum()

np.int64(0)

In [22]:
from shapely.geometry import Point, Polygon, MultiPolygon

# Define a function to convert GEO to appropriate geometry type
def geo_to_geometry(geo_json_str):
    try:
        # Parse the JSON string
        data = json.loads(geo_json_str)
        coordinates = data.get('coordinates', None)

        # Check if coordinates exist
        if coordinates:
            # Handle simple Point geometry
            if len(coordinates) == 2 and isinstance(coordinates[0], (float, int)):
                return Point(coordinates)
            
            # Handle Polygon or MultiPolygon geometries based on nesting
            elif isinstance(coordinates[0][0], list):  # Nested lists indicate Polygon
                if len(coordinates[0][0]) == 2:  # Polygon
                    return Polygon(coordinates[0])
                else:  # MultiPolygon
                    return MultiPolygon([Polygon(poly) for poly in coordinates])
            elif len(coordinates) == 1:  # Edge case for nested polygons with single length
                return Polygon(coordinates[0])
        
        return None  # Return None if structure is invalid or unsupported
    except (json.JSONDecodeError, ValueError, TypeError) as e:
        print(f"Error parsing: {geo_json_str} -> {e}")
        return None

# Apply the function to the 'GEO' column to create the 'geometry' column
df['geometry'] = df['GEO'].apply(geo_to_geometry)

# Now the 'geometry' column contains Point, Polygon, or MultiPolygon objects
print(df[['GEO', 'geometry']].head())


Error parsing: {"coordinates":[[[[-121.62471099999999,36.81248400000004],[-121.623059,36.81543700000004],[-121.61882,36.815735000000004],[-121.61954600000003,36.822429],[-121.63046299999993,36.82139900000004],[-121.62817499999998,36.82653200000002],[-121.63022199999999,36.83403399999999],[-121.63884899999995,36.82981800000003],[-121.64227899999999,36.83820900000002],[-121.65017099999999,36.83434399999997],[-121.669664,36.83435300000001],[-121.68706800000001,36.861006000000025],[-121.693339,36.85944500000001],[-121.69418300000002,36.856846],[-121.69030299999997,36.851983999999966],[-121.70166099999996,36.848571000000014],[-121.70211199999997,36.845616000000035],[-121.698161,36.83884900000004],[-121.70730099999996,36.84016400000004],[-121.71030799999998,36.842831],[-121.71041700000004,36.84590299999998],[-121.73366499999996,36.83883199999996],[-121.73208199999999,36.83686600000001],[-121.73443799999997,36.83041600000004],[-121.73313399999999,36.829149000000015],[-121.74094839938428,36.82

In [20]:
import json
import pandas as pd

# Define a function to check the structure of each entry in the 'GEO' column
def inspect_geo_pattern(geo_json_str):
    try:
        # Parse the JSON string
        data = json.loads(geo_json_str)
        # Capture the structure type
        if isinstance(data, dict) and 'coordinates' in data:
            coordinates = data['coordinates']
            # Return the type of coordinates and their length
            return f"coordinates_type: {type(coordinates)}, length: {len(coordinates)}"
        else:
            return "Invalid structure"
    except (json.JSONDecodeError, ValueError, TypeError) as e:
        return f"Error: {e}"

# Apply the inspection function to the 'GEO' column
df['geo_pattern'] = df['GEO'].apply(inspect_geo_pattern)

# Show the unique patterns and their counts
pattern_counts = df['geo_pattern'].value_counts()

# Display the patterns
print("Different patterns in the 'GEO' column:")
print(pattern_counts)

# Optionally, display rows with unusual patterns
print("\nRows with unusual 'GEO' patterns:")
display(df[df['geo_pattern'] != 'coordinates_type: <class \'list\'>, length: 2'][['GEO', 'geo_pattern']].head())


Different patterns in the 'GEO' column:
geo_pattern
coordinates_type: <class 'list'>, length: 1     11493
coordinates_type: <class 'list'>, length: 2      7885
coordinates_type: <class 'list'>, length: 3       212
coordinates_type: <class 'list'>, length: 4       186
coordinates_type: <class 'list'>, length: 6        73
coordinates_type: <class 'list'>, length: 7        49
coordinates_type: <class 'list'>, length: 5        47
coordinates_type: <class 'list'>, length: 11       32
coordinates_type: <class 'list'>, length: 24       18
coordinates_type: <class 'list'>, length: 10       16
coordinates_type: <class 'list'>, length: 20       16
coordinates_type: <class 'list'>, length: 15       16
coordinates_type: <class 'list'>, length: 42       14
coordinates_type: <class 'list'>, length: 8        13
Name: count, dtype: int64

Rows with unusual 'GEO' patterns:


GEO  \
2  {"coordinates":[[[[-121.62471099999999,36.8124...   
3  {"coordinates":[[[-120.760378,36.2030850000000...   
6  {"coordinates":[[[-122.90203199999996,40.69420...   
7  {"coordinates":[[[-118.073322,34.0905600000000...   
8  {"coordinates":[[[-121.95352099999997,37.07623...   

                                   geo_pattern  
2  coordinates_type: <class 'list'>, length: 4  
3  coordinates_type: <class 'list'>, length: 1  
6  coordinates_type: <class 'list'>, length: 1  
7  coordinates_type: <class 'list'>, length: 1  
8  coordinates_type: <class 'list'>, length: 1

In [9]:
df['geometry'].isna().sum()

np.int64(20070)

In [ ]:

def assign_cbgid(df, shapefile):
    # Apply json.loads only if the entry is a string
    df['GEO'] = df['GEO'].apply(
        lambda x: json.loads(x) if isinstance(x, str) else x
    )

    # Create a 'geometry' column
    df['geometry'] = df['GEO'].apply(create_point)

    # Convert to GeoDataFrame and set the initial CRS (assuming WGS84)
    gdf_events = gpd.GeoDataFrame(df, geometry='geometry', crs="EPSG:4326")

    # Now you can transform it to another CRS (or keep it as is, since EPSG:4326 is WGS84)
    gdf_events['geometry'] = gdf_events['geometry'].to_crs(epsg=4326)

    # # Print the results to verify
    # print(gdf_events['geometry'].head())

    # Perform spatial join between the event points and the polygon census block groups
    gdf_with_cbgid = gpd.sjoin(gdf_events, poly, how='left', predicate='within')

    # Merge the original df_attended_events with the gdf_with_cbgid based on 'EVENT_ID'
    merged_events = df.merge(
        gdf_with_cbgid[['EVENT_ID', 'GEOID']],  # Selecting only relevant columns
        on='EVENT_ID',  # Merging on 'EVENT_ID'
        how='left'  # Keep all rows from the original DataFrame
    )

    return merged_events